In [14]:
import pandas as pd
import numpy as np
import plotly.offline as py
import plotly.graph_objs as go
import plotly.figure_factory as FF
py.init_notebook_mode()

import gensim
from gensim.models import LdaModel
from gensim.corpora import Dictionary, MmCorpus

df_fake = pd.read_csv('fake.csv')
df_fake[['title', 'text', 'language']].head()
df_fake = df_fake.loc[(pd.notnull(df_fake.text)) & (df_fake.language == 'english')]
df_fake.shape

(12357, 20)

In [2]:
from gensim.parsing.preprocessing import remove_stopwords, strip_punctuation
import gensim
import re
from gensim.models import LdaModel
from gensim.corpora import Dictionary, MmCorpus

# remove stopwords and punctuations
def preprocess(row):
    return strip_punctuation(remove_stopwords(row.lower()))
    
df_fake['text'] = df_fake['text'].apply(preprocess)

# Convert data to required input format by LDA
texts = []
for line in df_fake.text:
    lowered = line.lower()
    words = re.findall(r'\w+', lowered, flags = re.UNICODE | re.LOCALE)
    texts.append(words)

vocabulary = Dictionary(texts)
vocabulary.filter_extremes(no_below=3, no_above=0.5)

In [3]:
len(vocabulary)

42038

In [4]:
MmCorpus.serialize('./fake_news.mm', (vocabulary.doc2bow(doc) for doc in texts))
vocabulary.save('./fake_news.vocab')
del texts
corpus_fake = MmCorpus('./fake_news.mm')

In [38]:
lda_fake = LdaModel(corpus=corpus_fake, id2word=vocabulary, num_topics=35, chunksize=1500, iterations=200, alpha='auto')

In [7]:
# lda_fake = LdaModel.load('fake_news_35.lda')

In [41]:
import pyLDAvis as ldavis
import pyLDAvis.gensim

ldavis.enable_notebook()
prepared_data = ldavis.gensim.prepare(lda_fake, corpus_fake, vocabulary, sort_topics=False)
prepared_data

/Users/parul/.virtualenvs/gensim3/lib/python3.4/site-packages/pyLDAvis/_prepare.py:387: DeprecationWarning:


.ix is deprecated. Please use
.loc for label based indexing or
.iloc for positional indexing

See the documentation here:
http://pandas.pydata.org/pandas-docs/stable/indexing.html#deprecate_ix



PreparedData(topic_coordinates=           Freq  cluster  topics         x         y
topic                                               
0      1.727599        1       1 -0.190427 -0.035339
1      0.954588        1       2 -0.039475 -0.002620
2      4.607540        1       3  0.071461 -0.074794
3      2.140290        1       4 -0.024143 -0.027555
4      3.840464        1       5 -0.028094  0.070128
5      1.947461        1       6 -0.007430 -0.011830
6      1.005861        1       7 -0.069121 -0.002146
7      4.361692        1       8 -0.066971 -0.047140
8      4.905292        1       9 -0.055979 -0.023900
9      1.791259        1      10 -0.058051  0.033300
10     0.808243        1      11  0.077096 -0.100543
11     1.694303        1      12 -0.144555 -0.001197
12     4.448146        1      13  0.077451 -0.100634
13     2.883261        1      14  0.129251  0.041628
14     6.085480        1      15  0.099502 -0.074269
15     1.648262        1      16 -0.124468  0.021442
16     1.139607        1      17  0.028262  0.117719
17     1.638859        1      18  0.062684  0.164921
18     5.099368        1      19  0.083557 -0.071048
19     3.381769        1      20  0.048673 -0.105512
20     1.800661        1      21  0.122290  0.180874
21     9.432056        1      22 -0.044434 -0.118196
22     1.519721        1      23 -0.245999  0.083197
23     4.466833        1      24  0.022307 -0.037783
24     7.191937        1      25  0.081772 -0.163525
25     2.663673        1      26  0.018138  0.037382
26     1.905942        1      27 -0.053932  0.124176
27     0.877029        1      28  0.064952  0.033380
28     5.064335        1      29  0.134216  0.125305
29     1.662630        1      30  0.065202 -0.105667
30     1.361863        1      31  0.087406  0.063252
31     1.678109        1      32 -0.097493 -0.071386
32     2.312102        1      33  0.099416  0.089674
33     0.947694        1      34  0.021206 -0.044253
34     1.006069        1      35 -0.144271  0.032959, topic_info=      Category          Freq            Term         Total  loglift  logprob
term                                                                        
20807  Default  23879.000000           trump  23879.000000  30.0000  30.0000
4379   Default  22628.000000         clinton  22628.000000  29.0000  29.0000
27245  Default   8144.000000          russia   8144.000000  28.0000  28.0000
41469  Default   5891.000000             fbi   5891.000000  27.0000  27.0000
37674  Default   5178.000000             com   5178.000000  26.0000  26.0000
27609  Default  14995.000000         hillary  14995.000000  25.0000  25.0000
31974  Default   5058.000000         russian   5058.000000  24.0000  24.0000
28053  Default  10038.000000        election  10038.000000  23.0000  23.0000
36829  Default   9214.000000             war   9214.000000  22.0000  22.0000
18885  Default   4864.000000           syria   4864.000000  21.0000  21.0000
15396  Default   4056.000000          police   4056.000000  20.0000  20.0000
27973  Default   2071.000000          israel   2071.000000  19.0000  19.0000
23700  Default   6056.000000          donald   6056.000000  18.0000  18.0000
28366  Default   3800.000000           women   3800.000000  17.0000  17.0000
38116  Default  15885.000000            said  15885.000000  16.0000  16.0000
20596  Default   5434.000000        military   5434.000000  15.0000  15.0000
20718  Default   4299.000000          emails   4299.000000  14.0000  14.0000
13291  Default   3019.000000          health   3019.000000  13.0000  13.0000
27497  Default   3598.000000           water   3598.000000  12.0000  12.0000
37944  Default   2580.000000           comey   2580.000000  11.0000  11.0000
14849  Default   3388.000000   investigation   3388.000000  10.0000  10.0000
36903  Default   2637.000000         nuclear   2637.000000   9.0000   9.0000
13767  Default   9366.000000           obama   9366.000000   8.0000   8.0000
19878  Default   6032.000000               1   6032.000000   7.0000   7

In [15]:
def plot_difference(mdiff, title="", annotation=None):
    """
    Helper function for plot difference between models
    """
    annotation_html = None
    if annotation is not None:
        annotation_html = [["+++ {}<br>--- {}".format(", ".join(int_tokens), 
                                              ", ".join(diff_tokens)) 
                            for (int_tokens, diff_tokens) in row] 
                           for row in annotation]
        
    data = go.Heatmap(z=mdiff, colorscale='RdBu', text=annotation_html)
    layout = go.Layout(width=950, height=950, title=title,
                       xaxis=dict(title="topic"), yaxis=dict(title="topic"))
    py.iplot(dict(data=[data], layout=layout))

In [16]:
mdiff, annotation = lda_fake.diff(lda_fake, distance='jenson_shannon', num_words=50)
plot_difference(mdiff, title="Topic difference [jenson_shannon distance]", annotation=annotation)